In [ ]:
#IV Load the data for a station and organize for precipitation model
#Check for update
import os as os
import pandas as pd
import numpy as np
import math
from datetime import datetime
import pyarrow as pa
import pyarrow.parquet as pq
import matplotlib.pyplot as plt
import csv
from functools import reduce

In [2]:
#Paths
#Need to set up based on who is running
usr = "JH"
if usr == "PK":
    ipd01 = "\\\\CXA01\\Users\\jhugh\\Documents\\HT\\NCEI_data\\2024\\"
    ipd02 = "D:\\CodeLibrary\\Python\\weathermetrics\\data\\weathermetrics\\"
    ipd03 = ""
    ipd04 = ""
    
if usr == "JH":
    ipd01 = "\\\\CXA01\\Users\\jhugh\\Documents\\HT\\NCEI_data\\2024\\"
    ipd02 = "\\\\CXA01\\Users\\jhugh\\Documents\\HT\\NCEI_data\\metrics_csv\\"
    ipd03 = "\\\\CXA01\\Users\\jhugh\\Documents\\Py_S4\\Py_S4_v02_JHH\\NCEI_data\\"
    ipd04 = "\\\\CXA01\\Users\\jhugh\\Documents\\Py_S4\\Py_S4_v02_JHH\\NCEI_parquet_files\\"


In [3]:
def fn_select_data_vectors_pr07(stid_keys,nstations,nhours,nmonths_row,nmonths_col):
    #Get the matrix of data to input into marix
    #The S4 model
    # 1. Read in combined data files for multiple stations
    # 2. Find the common dates that will be used to align the matrices
    #    Keep only the values that fit the common starting date 

    # 1. Read in data files and get start date v_date... for each
    # Check that data exist for all metrics

    df_stid = stid_keys
    df_stid2 = df_stid.iloc[:, [1]]
    df_stid2 = df_stid2.drop_duplicates() # unique()
    
    n_rows_stid = min(len(df_stid2),nstations)
    
    #Matrix in which measures are stored
    n_vmt_rows = nhours*30*max(nmonths_row,nmonths_col)
    
    data_list = []
    date_max_list =[]
    
    #1. Read in data files
    for i in range(0, n_rows_stid):
    #for i in range(0, 28):
        infile = ipd03 + str(df_stid2.iloc[i,0]) + "_model_data_combined.csv"
        print(infile)
        
        #Eliminate fully blank lines
        cleaned_lines = []
        with open(infile, 'r', newline='') as infile:
            reader = csv.reader(infile)
            for row in reader:
                # Example: Skip rows that are entirely empty or have only blank 'name'
                if any(cell.strip() for cell in row) and (len(row) < 1 or row[0].strip() != ''): # Assuming 'name' is the first column
                    cleaned_lines.append(row)
        
        df_metrics = pd.DataFrame(cleaned_lines[1:], columns=cleaned_lines[0]) # Assuming first row is header

        df_metrics['str_hr'] = df_metrics['nHOUR']  #.apply(lambda x: f'{x:02d}')
        df_metrics['date_hr'] = pd.to_datetime(df_metrics['Date_YYYYMMDD'] + ' ' + df_metrics['str_hr'])
        df_metrics['month_number'] = df_metrics['date_hr'].dt.month
        df_metrics['week_number'] = df_metrics['date_hr'].dt.isocalendar().week
        df_metrics['stid'] = str(df_stid2.iloc[i,0])
        data_list.append(df_metrics)

    #2. Align dates across data files
    for i in range(0, n_rows_stid):
        df = data_list[i]
        max_date = max(df['date_hr'])     
        date_max_list.append(max_date)
    
    date_filter = min(date_max_list)

    for i in range(0, n_rows_stid):
        df = data_list[i]

        filtered_df = df[df['date_hr'] < date_filter]
        filtered_df = filtered_df.iloc[(len(filtered_df) - n_vmt_rows):len(filtered_df)]
        
        idx_col = filtered_df.columns
        idx_col = str(df_stid2.iloc[i,0]) + '_' + idx_col
        filtered_df.columns = idx_col

        print(filtered_df.shape)
        
        data_list[i] = filtered_df
        
    return data_list[0:n_rows_stid]

In [4]:
def fn_create_data_matrix_pr07(lst_data,tgt_metric,nstations,nmetrics,nmonths_col,ndays_col):
    #Create a matrix for precipitation data that feeds
    #The S4 model
    # 1. Get data list and select target metric
    #Two choices now
    #    - prec
    #    - temp
    # 2.  Create output and move data into approprate cells

    # 1. get data list details and reduce to metrics
    data_vectors_list = []
    dt_rows = len(lst_data[0])
    df00 = []

    dt_rows_minus_1 = dt_rows - 1
    
    if tgt_metric == "prec": tgt_cols = [10,2,3,4,5,6,8,9,11,12]
    if tgt_metric == "temp": tgt_cols = [10,3,2,4,5,6,8,9,11,12]
    non_metrics = 4  #These are the non sensor data brought in to analysis (e.g., day of year, month, ...)
    
    #Reset the indices as all records are ordered by date and hour
    #But stations have missing records so not everything aligns
    #Need to use the target station (station 0) as the standard and left join th other fields
    for i in range(nstations):
        if i == 0:
            tdt = lst_data[i].iloc[:,tgt_cols]
        if i > 0:
            tdt = lst_data[i].iloc[:,tgt_cols[0:6]]
        tdt = tdt.iloc[::-1]
        tdt.reset_index(drop=True, inplace=True)
        first_column_name = tdt.columns[0]
        tdt.rename(columns={first_column_name: 'key_date_hr'}, inplace=True)
        df00.append(tdt)
        fn = f"1. Done with setting up station -  {i}"
        print(fn)
        #print(tdt)
        
    
    #Take the list of station data, df00, and paste side by side
    #to produce rs which is a large matrix of data for all stations 
    join_key = 'key_date_hr'
    rs = reduce(lambda left, right: pd.merge(left, right, on=join_key, how='left'), df00)
    
    #rs has each row being a dayXhour for all stations for the stations full metrics
    fn = f"2. Shape of combined data including all stations"
    print(fn)
    print(rs.shape)
    
    
    #2. Create output matrix and move data into appropriate cells
    #Note: target cells get 9 elements, feature cells get 5 elements
    
    nmetrics_and_non_metrics = nmetrics + non_metrics
    fn = f"nmetrics_and_non_metrics {nmetrics_and_non_metrics}"
    print(fn)
    ndataelements = nmetrics_and_non_metrics + (nstations-1)*(nmetrics)
    fn = f"ndataelements - stations by metrics {ndataelements}"
    print(fn)
    mt_cols = 1 + ndataelements*ndays_col*24
    fn = f"mt_cols 1 + #data elements*ndays_col*24 {mt_cols}"
    print(fn)
    mt_rows = len(rs)
    
    #mt_rows = 170000  #keep here for development until done
    mt_full_set = np.empty((mt_rows,mt_cols),np.float16)
    
    #Create matrix of data
    for i in range(0,mt_rows):
        mt_full_set[i,range(0,ndataelements)] = rs.iloc[i,range(1,ndataelements+1)].apply(pd.to_numeric, errors='coerce')
    
    fn = f"3. Full mt setup with initial data for the dayXhour only"
    print(fn)  
    print(mt_full_set.shape)
    
    #Add additional column sets
    lpi = mt_rows - ndays_col*24 - 1  #number of rows in rs matrix - the data elements in a column... 
                                      #ensures all records have data
    
    #limit of rows in data set so all matrix rows have data
    lpj = ndays_col*24 -1   #number of colum sets to fill, each with 104 columns
        
    
    #The row I am operating on
    for i in range(0,lpi):
        #The columns I am going to fill
        for j in range(0,lpj):
        
            row_get = i + j + 1              #For every new column in current row we have to go down one more row
            col_get_start = 0                #data retrieved starting column 1
            col_get_end = ndataelements - 1
            
            row_put = i
            col_put_start = ndataelements*(row_get - row_put)
            col_put_end = col_put_start + ndataelements - 1
            
            mt_full_set[row_put,col_put_start:col_put_end] = mt_full_set[row_get,col_get_start:col_get_end]
    
    fn = f"4. mt_full_set with ndays of data added to the columns"
    print(fn)  
    print(mt_full_set.shape)
     
    return mt_full_set #rs #mt_full_set

In [5]:
#functions to identify stations in network that have rain sensor and rain
def cnt_ge0(row):
        cnt_gt_0 = sum(row >= 0)
        return cnt_gt_0

def cnt_gt0(row):
        cnt_gt_0 = sum(row > 0)
        return cnt_gt_0

In [6]:
def fn_prec_ex01_orig(mtx01,nstations,nmetrics,dayscol):
    
    df = pd.DataFrame(mtx01)
    ncols_orig = df.shape[1]
    print(f"Number of mxt columns {ncols_orig}")
    
    
    #Does target have a finite value
    #df['tgt_isfinite'] = np.isfinite(df.iloc[:,0])
    
    #moving average of target value
    #window_hrs = 6
    #nm1 = 'tgt_roll_sum_per' + str(window_hrs)
    #df[nm1] = df.iloc[:,0].rolling(window=window_hrs, min_periods=1).sum()
    #nm2 = 'tgt_roll_round_int' + str(window_hrs)
    #df[nm2] = round(df[nm1],0)
    
    #nstations = 20
    #dayscol = 7
    #nmetrics = 5
    offset = 4  #additional fields for target station
    data_columns_start = (nmetrics + offset) + (nstations - 1)*nmetrics
    print(f"data_columns_start {data_columns_start}")
    
    curr_per = 1   #current period for which average is to be taken, must be 1 or greater
    tot_per = (dayscol*24 - 1)  #days by 24 hours minus 1
    
    #tot_per  = 4
    
    for iper in range(1,tot_per,1):

        vc_start1 = np.array([(iper*nstations*(nmetrics) + (iper*offset))])
        vc_start2 = vc_start1 + nmetrics + offset   #first set has day/month/week/hr info
        vc_end = vc_start2 + (nstations-1)*nmetrics
        vc_s2_end = np.arange(vc_start2,vc_end,nmetrics)

        vc_num = np.concatenate([vc_start1,vc_s2_end])

        nm = 'avg'+ str(iper)
        df[nm] = df.iloc[:,vc_num].mean(axis=1,skipna=True)

        nm = 'cnt_ge_zero'+ str(iper)
        jjge0 = df.iloc[:,vc_num].apply(cnt_ge0,axis=1)
        df[nm] = jjge0

        nm = 'cnt_gt_zero'+ str(iper)
        jjgt0 = df.iloc[:,vc_num].apply(cnt_gt0,axis=1)
        df[nm] = jjgt0
    
    ncols_final = df.shape[1]
    print(f"Final shape {ncols_final}")
    new_cols = range(ncols_orig,ncols_final,1)
    print(f"New columns {new_cols}")
    old_cols = range(data_columns_start,ncols_orig,1)
    print(f"Old columns {old_cols}")
    vc_keep = [0]+list(new_cols) + list(old_cols)
    print(f"Final columns {ncols_final}")
    
    #rtn_df = df  #df.iloc[:,vc_keep]
    #rtn_df = rtn_df.iloc[0:70000,vc_keep]
    dfs1 = df.iloc[:,[0,5,6,7,8]]
    #dfs2 = df.iloc[:,old_cols]
    dfs3 = df.iloc[:,new_cols]
    #dfs3.insert(0,'tgt',dfs1)
    
    del df
    df_out = pd.concat([dfs1,dfs3],axis=1)
        
    return df_out

In [7]:
def fn_prec_ex01(mtx01,nstations,nmetrics,dayscol):
    
    df = pd.DataFrame(mtx01).reset_index(drop=True)
    ncols_orig = df.shape[1]
    print(f"Number of mxt columns {ncols_orig}")
    
    #nstations = 20
    #dayscol = 7
    #nmetrics = 5
    offset = 4  #additional fields for target station
    data_columns_start = (nmetrics + offset) + (nstations - 1)*nmetrics
    print(f"data_columns_start {data_columns_start}")
    
    curr_per = 1   #current period for which average is to be taken, must be 1 or greater
    tot_per = (dayscol*24 - 1)  #days by 24 hours minus 1
    
    for iper in range(1,tot_per,1):

        vc_start1 = np.array([(iper*nstations*(nmetrics) + (iper*offset))])
        vc_start2 = vc_start1 + nmetrics + offset   #first set has day/month/week/hr info
        vc_end = vc_start2 + (nstations-1)*nmetrics
        
        vc_s2_end = np.arange(vc_start2.item(),vc_end.item(),nmetrics)
        
        vc_num = np.concatenate([vc_start1,vc_s2_end])

        nm1 = 'avg'+ str(iper)
        pds1 = df.iloc[:,vc_num].mean(axis=1,skipna=True)
        df[nm1] = pds1
        
        nm2 = 'cnt_ge_zero'+ str(iper)
        pds2 = df.iloc[:,vc_num].apply(cnt_ge0,axis=1)
        df[nm2] = pds2
        
        nm3 = 'cnt_gt_zero'+ str(iper)
        pds3 = df.iloc[:,vc_num].apply(cnt_gt0,axis=1)
        df[nm3] = pds3
                
    ncols_final = df.shape[1]
    print(f"Final shape {ncols_final}")
    new_cols = range(ncols_orig,ncols_final,1)
    print(f"New columns {new_cols}")
    old_cols = range(data_columns_start,ncols_orig,1)
    print(f"Old columns {old_cols}")
    vc_keep = [0]+list(new_cols) + list(old_cols)
    print(f"Final columns {ncols_final}")
    
    
    df_out = pd.concat([df.iloc[:,[0,5,6,7,8]],df.iloc[:,new_cols],df.iloc[:,old_cols]],axis=1)
        
    return df_out

In [8]:
def fn_create_tgt_matrix_pr07(mtx_data,tgt_metric,tgt_mod,nstations,nmetrics,ndays_col):
    
    mtx01 = mtx_data #.iloc[0:1000,:]
    nrows = mtx01.shape[0]
    ncols = mtx01.shape[1]
    
       
    if tgt_metric == "prec" and tgt_mod == "prec_ex01": 
        rtn_matrix = fn_prec_ex01(mtx01,nstations,nmetrics,ndays_col)
    
    
    #return the matrix for analysis
    return rtn_matrix

In [9]:
def fn_get_nearby_stations(stid_target, target_file,in_wd):

    dt01 = target_file[target_file['tgt_stid']==stid_target]
    dt01 = dt01[['feat_stid','dist_km']]
    
    vc_stid = dt01['feat_stid'].to_numpy()
    vc_stid = np.insert(vc_stid,0,tgt_stid)
    #vc_stid = [stid_target] + [vc_stid]
    
    #Need to create more combined data sets
    lst_files = os.listdir(in_wd)
    df_files = pd.DataFrame(lst_files,columns=["files"])
    df_files['stid'] = df_files['files'].str[:11]
    df_files['istarget'] = df_files['stid'].str.contains(stid_target,case=False)
    df_files['file_type'] = df_files['files'].str[23:31]
    df_files['isintarget'] = df_files['stid'].isin(vc_stid)
    
    df_files = df_files[df_files['file_type']=="combined"]
    df_files = df_files[df_files['isintarget']==True]
    
    mrg_df = pd.merge(df_files, dt01,how='left',left_on='stid',right_on='feat_stid')
    mrg_df = mrg_df.drop(columns=['feat_stid','isintarget','file_type'])
    mrg_df = mrg_df.sort_values(by='dist_km',na_position='first')
    mrg_df = mrg_df.reset_index(drop=True)
    mrg_df.columns = ['fnames','st_id','is_target_station','dist_km']
    
    return mrg_df

In [22]:
#STEP 1.  Select a station using ID to get its related stations


#Load df of target stations and those close by
#74486094789 is JFK airport
#74486454787 is Farmingdale
#72505004781 is Macarthur
#72502014734 is Newark
#72427653859 is Dayton, OH
#72551014939 is Lincoln, NE
#Select the target station for which predictions will be made
dt_trg_set2 = ipd02 + "Station_Pairs_LE_100km_Info.csv"
dt_analysis_set2 = pd.read_csv(dt_trg_set2)
#Governs the target station in subsequent modules
tgt_stid =  "72551014939"

#Nearby stations within 100km
dt_analysis_set_keys = fn_get_nearby_stations(tgt_stid,dt_analysis_set2,ipd03)

nstations_in_100km = len(dt_analysis_set_keys) #number of stations within 100 km
num_st_keep = 20   #num of stations to keep for analysis
nstations = min(nstations_in_100km,num_st_keep)

#analysis_set = dt_trg_set
#dt_analysis_set = pd.read_csv(analysis_set)
#dt_analysis_set['path'] = ipd02
#dt01 = dt_analysis_set[dt_analysis_set['target_station']==int(st_id)]
#uniq_stat = dt01['vect_close_bkt2'].unique()[:2]
#uniq_station = dt01['st_id'].unique()[:num_st_keep]
#dt02 = dt01[dt01['st_id'].isin(uniq_station)]

dt_analysis_set_keys


fnames        st_id  is_target_station  \
0   72551014939_model_data_combined.csv  72551014939               True   
1   99999994995_model_data_combined.csv  99999994995              False   
2   99999994996_model_data_combined.csv  99999994996              False   
3   72094200323_model_data_combined.csv  72094200323              False   
4   72551594947_model_data_combined.csv  72551594947              False   
5   72030804992_model_data_combined.csv  72030804992              False   
6   72556404924_model_data_combined.csv  72556404924              False   
7   72229100470_model_data_combined.csv  72229100470              False   
8   72551214989_model_data_combined.csv  72551214989              False   
9   72554014949_model_data_combined.csv  72554014949              False   
10  72554104993_model_data_combined.csv  72554104993              False   
11  72556594951_model_data_combined.csv  72556594951              False   
12  72040500436_model_data_combined.csv  72040500436              False   
13  72550014942_model_data_combined.csv  72550014942              False   

      dist_km  
0         NaN  
1   16.805356  
2   18.565925  
3   45.053080  
4   60.834025  
5   67.145461  
6   69.984464  
7   72.169586  
8   72.673999  
9   77.292347  
10  80.624573  
11  82.529526  
12  83.461669  
13  88.939160

In [23]:
#STEP 2.  Use elements created in STEP 1 to get a data matrix for analysis
#All the available stations which have all three metrics needed for model
#vc_stid = dt_analysis_set_keys[['st_id']].drop_duplicates()

#Organize the data based on the nature of the data so they all conform to the same size matrices
#The metrics included are
#  AT - air temperature in Celcius
#  RH - relative humidity in Percent
#  PR - precipitation in MM

#Put them all in appropriate matrices and create list of metrics
#Data files are of two types
#    -  24 hour * 365 days * n years  (AT, PR)
#    -  365 days * n years (RH)

#Parameters governing data matrix
stid_target = tgt_stid
stid_keys = dt_analysis_set_keys

ipd = ipd02
nhours = 24
ndays = 365
nmonths_row = 240
nmonths_col = 2 #governs the number of months predicting that are needed
ndays_col = 3  #governs the number of days predicting that are needed
nmetrics = 5
tgt_metric =  "prec" #"prec"  "temp"
tgt_mod = "prec_ex01"


In [24]:

#1. Get the relevant data in a list
lst_data = fn_select_data_vectors_pr07(stid_keys,nstations,nhours,nmonths_row,nmonths_col)
fn = f"lst data done"
print(fn)


\\CXA01\Users\jhugh\Documents\Py_S4\Py_S4_v02_JHH\NCEI_data\72551014939_model_data_combined.csv
\\CXA01\Users\jhugh\Documents\Py_S4\Py_S4_v02_JHH\NCEI_data\99999994995_model_data_combined.csv
\\CXA01\Users\jhugh\Documents\Py_S4\Py_S4_v02_JHH\NCEI_data\99999994996_model_data_combined.csv
\\CXA01\Users\jhugh\Documents\Py_S4\Py_S4_v02_JHH\NCEI_data\72094200323_model_data_combined.csv
\\CXA01\Users\jhugh\Documents\Py_S4\Py_S4_v02_JHH\NCEI_data\72551594947_model_data_combined.csv
\\CXA01\Users\jhugh\Documents\Py_S4\Py_S4_v02_JHH\NCEI_data\72030804992_model_data_combined.csv
\\CXA01\Users\jhugh\Documents\Py_S4\Py_S4_v02_JHH\NCEI_data\72556404924_model_data_combined.csv
\\CXA01\Users\jhugh\Documents\Py_S4\Py_S4_v02_JHH\NCEI_data\72229100470_model_data_combined.csv
\\CXA01\Users\jhugh\Documents\Py_S4\Py_S4_v02_JHH\NCEI_data\72551214989_model_data_combined.csv
\\CXA01\Users\jhugh\Documents\Py_S4\Py_S4_v02_JHH\NCEI_data\72554014949_model_data_combined.csv
\\CXA01\Users\jhugh\Documents\Py_S4\Py_S

In [25]:

#2. Construct a matrix from most recent to most distant from the list data
mtx_data = fn_create_data_matrix_pr07(lst_data,tgt_metric,nstations,nmetrics,nmonths_col,ndays_col)
fn = f"mtx data done"
print(fn)

#Save the mtx_data to a folder
#This lets us start at Step 3 for iterative runs
print(ipd04)
rtn_mtx_pqt = pd.DataFrame(mtx_data)
print(rtn_mtx_pqt.shape)
fn = f"{ipd04}{tgt_metric}_mtx_{stid_target}_stations_{nstations}_RowMn_{nmonths_row}_ColDy_{ndays_col}.parquet"
print(fn)
rtn_mtx_pqt.to_parquet(fn, index=False)



1. Done with setting up station -  0
1. Done with setting up station -  1
1. Done with setting up station -  2
1. Done with setting up station -  3
1. Done with setting up station -  4
1. Done with setting up station -  5
1. Done with setting up station -  6
1. Done with setting up station -  7
1. Done with setting up station -  8
1. Done with setting up station -  9
1. Done with setting up station -  10
1. Done with setting up station -  11
1. Done with setting up station -  12
1. Done with setting up station -  13
2. Shape of combined data including all stations
(172800, 75)
nmetrics_and_non_metrics 9
ndataelements - stations by metrics 74
mt_cols 1 + #data elements*ndays_col*24 5329
3. Full mt setup with initial data for the dayXhour only
(172800, 5329)
4. mt_full_set with ndays of data added to the columns
(172800, 5329)
mtx data done
\\CXA01\Users\jhugh\Documents\Py_S4\Py_S4_v02_JHH\NCEI_parquet_files\
(172800, 5329)
\\CXA01\Users\jhugh\Documents\Py_S4\Py_S4_v02_JHH\NCEI_parquet_f

In [ ]:
#3.  Read in mtx_data file

#Get the mtx_data from a folder
#This lets us start at Step 3 for iterative runs
fn = '\\\\CXA01\\Users\\jhugh\\Documents\\Py_S4\\Py_S4_v02_JHH\\NCEI_parquet_files\\prec_mtx_74486094789_stations_20_RowMn_240_ColDy_7.parquet'

# Read the Parquet file into a Pandas DataFrame
mtx_data = pd.read_parquet(fn)
print(mtx_data.shape)


(172800, 17473)


In [26]:
#3.  Create a target variable and select feature variables

s4_data = fn_create_tgt_matrix_pr07(mtx_data,"prec","prec_ex01",nstations,nmetrics,ndays_col)

print(f"Shape of s4_data {s4_data.shape}")
fn = f"s4 data done"
print(fn)
s4_data

Number of mxt columns 5329
data_columns_start 74


C:\Users\jhugh\AppData\Local\Temp\ipykernel_23548\1885214214.py:29: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[nm1] = pds1
C:\Users\jhugh\AppData\Local\Temp\ipykernel_23548\1885214214.py:33: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[nm2] = pds2
C:\Users\jhugh\AppData\Local\Temp\ipykernel_23548\1885214214.py:37: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) 

Final shape 5539
New columns range(5329, 5539)
Old columns range(74, 5329)
Final columns 5539
Shape of s4_data (172800, 5470)
s4 data done


0      5     6     7     8  avg1  cnt_ge_zero1  cnt_gt_zero1  avg2  \
0       NaN  366.0  22.0  12.0   1.0   NaN             0             0   NaN   
1       NaN  366.0  21.0  12.0   1.0   NaN             0             0   NaN   
2       NaN  366.0  20.0  12.0   1.0   NaN             0             0   NaN   
3       NaN  366.0  19.0  12.0   1.0   NaN             0             0   NaN   
4       NaN  366.0  18.0  12.0   1.0   NaN             0             0   NaN   
...     ...    ...   ...   ...   ...   ...           ...           ...   ...   
172795  0.0  106.0   3.0   4.0  15.0   0.0            14             0   0.0   
172796  0.0  106.0   2.0   4.0  15.0   0.0            14             0   0.0   
172797  0.0  106.0   1.0   4.0  15.0   0.0            14             0   0.0   
172798  0.0  106.0   0.0   4.0  15.0   0.0            14             0   0.0   
172799  0.0  105.0  23.0   4.0  15.0   0.0            14             0   0.0   

        cnt_ge_zero2  ...       5319  5320  5321  5322  5323       5324  5325  \
0                  0  ...   8.265625   NaN   NaN   NaN   NaN   7.199219   NaN   
1                  0  ...  10.765625   NaN   NaN   NaN   NaN   9.398438   NaN   
2                  0  ...  12.734375   NaN   NaN   NaN   NaN  11.398438   NaN   
3                  0  ...  12.796875   NaN   NaN   NaN   NaN  11.703125   NaN   
4                  0  ...  11.632812   NaN   NaN   NaN   NaN  10.601562   NaN   
...              ...  ...        ...   ...   ...   ...   ...        ...   ...   
172795            14  ...   0.000000   0.0   0.0   0.0   0.0   0.000000   0.0   
172796            14  ...   0.000000   0.0   0.0   0.0   0.0   0.000000   0.0   
172797            14  ...   0.000000   0.0   0.0   0.0   0.0   0.000000   0.0   
172798            14  ...   0.000000   0.0   0.0   0.0   0.0   0.000000   0.0   
172799            14  ...   0.000000   0.0   0.0   0.0   0.0   0.000000   0.0   

        5326  5327  5328  
0        NaN   0.0   0.0  
1        NaN   0.0   0.0  
2        NaN   0.0   0.0  
3        NaN   0.0   0.0  
4        NaN   0.0   0.0  
...      ...   ...   ...  
172795   0.0   0.0   0.0  
172796   0.0   0.0   0.0  
172797   0.0   0.0   0.0  
172798   0.0   0.0   0.0  
172799   0.0   0.0   0.0  

[172800 rows x 5470 columns]

In [27]:

#Save the s4_data to a folder
#This lets us start at Step 3 for iterative runs
print(f"Done temp")
print(ipd04)
rtn_s4_data_pqt = pd.DataFrame(s4_data)
print(rtn_s4_data_pqt.shape)
fn = f"{ipd04}{tgt_metric}_s4data_{stid_target}_stations_{nstations}_RowMn_{nmonths_row}_ColDy_{ndays_col}.parquet"
print(fn)
rtn_s4_data_pqt.to_parquet(fn, index=False)

Done temp
\\CXA01\Users\jhugh\Documents\Py_S4\Py_S4_v02_JHH\NCEI_parquet_files\
(172800, 5470)
\\CXA01\Users\jhugh\Documents\Py_S4\Py_S4_v02_JHH\NCEI_parquet_files\prec_s4data_72551014939_stations_14_RowMn_240_ColDy_3.parquet


In [15]:
#This lets us start at Step 3 for iterative runs
fn = '\\\\CXA01\\Users\\jhugh\\Documents\\Py_S4\\Py_S4_v02_JHH\\NCEI_parquet_files\\prec_s4data_72502014734_stations_20_RowMn_240_ColDy_3.parquet'

# Read the Parquet file into a Pandas DataFrame
s4_data = pd.read_parquet(fn)
print(s4_data.shape)




(172800, 7600)


In [28]:
def transform_matrix_precip(df, bins, labels):
    """
    Transforms the given matrix by binning the first column, dropping the first row and column,
    and adding the binned column as the first column.

    Parameters:
        matrix (pd.DataFrame): The input matrix.

    Returns:
        pd.DataFrame: The transformed matrix.
    """
    # Extract the first column (dependent variable)
    firstcolumn = df.iloc[:, 0].astype('float32')
    
    # Bin the first column
    binned_column = pd.cut(firstcolumn, bins=bins, labels=labels)
    
    # Add the binned column as the first column
    df.insert(0, 0, binned_column.iloc[0:].values)
    
    # Drop columns 1:3 the first first column
    df = df.drop(columns=df.columns[[3]])

    # Return the final matrix
    
    return df


In [ ]:
from sklearn.datasets import make_classification

# Set a random seed for reproducibility
np.random.seed(42)

# Generate a synthetic dataset
# n_samples: number of data points
# n_features: number of predictor variables
# n_informative: number of features that are actually informative
# n_classes: number of target classes (0, 1, 2)
# n_redundant: number of redundant features (linear combinations of informative features)
# n_repeated: number of repeated features (copies of informative features)
# random_state: seed for reproducibility
# class_sep: controls how separable the classes are (higher values mean stronger predictive power)
X, y = make_classification(n_samples=100000,
                           n_features=4,
                           n_informative=3,
                           n_classes=3,
                           n_redundant=0,
                           n_repeated=0,
                           random_state=42,
                           class_sep=1.5) # Adjust class_sep for moderate to strong predictive power

"""
# Scale predictor variables to be between 0 and 1
X_scaled = (X - X.min(axis=0)) / (X.max(axis=0) - X.min(axis=0))

# Create a Pandas DataFrame
df_fake = pd.DataFrame(X_scaled, columns=['predictor_1', 'predictor_2', 'predictor_3', 'predictor_4'])
df_fake['target'] = y


df_fake['target'] = df_fake['target'].astype('category')

df_fake['predictor_1'] = np.float32(df_fake['predictor_1'])
df_fake['predictor_2'] = np.float32(df_fake['predictor_2'])
df_fake['predictor_3'] = np.float32(df_fake['predictor_3'])
df_fake['predictor_4'] = np.float32(df_fake['predictor_4'])

df_fake = df_fake.iloc[:,[4,0,1,2,3]]

# Display the first few rows of the dataset
print(df_fake.head())
print(df_fake.shape)
print(df_fake.dtypes)


# Display value counts of the target variable to confirm distribution
print("\nTarget variable distribution:")
print(df_fake['target'].value_counts())

# Example usage
train_data, val_data, test_data = split_time_series_data(df_fake)
print("Training Set:", train_data.shape)
print("Validation Set:", val_data.shape)
print("Test Set:", test_data.shape)

# Export datasets to Parquet and CSV
train_data.to_parquet(f"{ipd04}fake_train.parquet", index=False)
val_data.to_parquet(f"{ipd04}fake_validation.parquet", index=False)
test_data.to_parquet(f"{ipd04}fake_test.parquet", index=False)

train_data.to_csv(f"{ipd04}fake_train.csv", index=False)
val_data.to_csv(f"{ipd04}fake_validation.csv", index=False)
test_data.to_csv(f"{ipd04}fake_test.csv", index=False)

df_fake
"""

'\n# Scale predictor variables to be between 0 and 1\nX_scaled = (X - X.min(axis=0)) / (X.max(axis=0) - X.min(axis=0))\n\n# Create a Pandas DataFrame\ndf_fake = pd.DataFrame(X_scaled, columns=[\'predictor_1\', \'predictor_2\', \'predictor_3\', \'predictor_4\'])\ndf_fake[\'target\'] = y\n\n\ndf_fake[\'target\'] = df_fake[\'target\'].astype(\'category\')\n\ndf_fake[\'predictor_1\'] = np.float32(df_fake[\'predictor_1\'])\ndf_fake[\'predictor_2\'] = np.float32(df_fake[\'predictor_2\'])\ndf_fake[\'predictor_3\'] = np.float32(df_fake[\'predictor_3\'])\ndf_fake[\'predictor_4\'] = np.float32(df_fake[\'predictor_4\'])\n\ndf_fake = df_fake.iloc[:,[4,0,1,2,3]]\n\n# Display the first few rows of the dataset\nprint(df_fake.head())\nprint(df_fake.shape)\nprint(df_fake.dtypes)\n\n\n# Display value counts of the target variable to confirm distribution\nprint("\nTarget variable distribution:")\nprint(df_fake[\'target\'].value_counts())\n\n# Example usage\ntrain_data, val_data, test_data = split_time_se

In [30]:
# Example usage
# Example matrix (replace this with your actual matrix)
df = pd.DataFrame(s4_data).iloc[1:,] # Convert to DataFrame and drop the first row for binning
print(df.shape)
##Only keep records w rain
#df = df[df.iloc[:,0]>0]
#print(df.shape)

#Drop rows where there has been no rain in total area for past 48 hours 
vc_num = [x for x in range(5,148,3)]
nm1 = 'sum_avg'
pds1 = df.iloc[:,vc_num].sum(axis=1,skipna=True)
df_area_non_zero = df[pds1 > 0]

#Drop rows where there has been no rain
df_area_non_zero_yrain = df_area_non_zero[df_area_non_zero.iloc[:,0]>0]
df_area_non_zero_nrain = df_area_non_zero[df_area_non_zero.iloc[:,0]==0]

df_sample_nrain = df_area_non_zero_nrain  #df_area_non_zero_nrain.sample(n=len(df_area_non_zero_yrain))
df_area_non_zero_ynrain = pd.concat((df_area_non_zero_yrain,df_sample_nrain),axis=0)

#Pick the df for analysis
dfs = df_area_non_zero_ynrain
print(f"Full rain and no rain {dfs.shape}")

del df, df_area_non_zero_yrain, df_area_non_zero_nrain, df_sample_nrain, df_area_non_zero_ynrain
        
# Drop rows where the first column has missing values
# df = df.dropna(subset=[0])
condition = np.isfinite(dfs.iloc[:,0])
df_subset = pd.DataFrame(dfs[condition])
del dfs
print(df_subset.shape)

bins = [-float('inf'),0.1,0.5,1,2,3,4,5,float('inf')]
# bins = [-float('inf'), 0] + list(pd.qcut(fc[fc > 0], q=4, retbins=True)[1][1:]) + [float('inf')]
labels = [0,0.1, 0.5,1,2,3,4,5]
print(bins, labels)

df_transformed = transform_matrix_precip(df_subset, bins, labels)

df_transformed.drop(columns=df_transformed.columns[1],inplace=True)
df_transformed.shape

df_transformed = df_transformed.sample(frac=1).reset_index(drop=True)


print("Analysis Set:", df_transformed.shape)
print(df_transformed[0].value_counts(dropna=False).sort_index())

df_transformed

(172799, 5470)
Full rain and no rain (97471, 5470)
(97471, 5470)
[-inf, 0.1, 0.5, 1, 2, 3, 4, 5, inf] [0, 0.1, 0.5, 1, 2, 3, 4, 5]


ValueError: cannot insert 0, already exists

In [20]:
def split_time_series_data(df, train_ratio=0.6, val_ratio=0.2, test_ratio=0.2):
    """
    Splits a time series dataset into training, validation, and test sets.

    Parameters:
        df (pd.DataFrame): The input time series dataset, ordered in descending dates.
        train_ratio (float): The proportion of data to use for training.
        val_ratio (float): The proportion of data to use for validation.
        test_ratio (float): The proportion of data to use for testing.

    Returns:
        tuple: A tuple containing three DataFrames (train, validation, test).
    """
    assert train_ratio + val_ratio + test_ratio == 1.0, "Ratios must sum to 1.0"

    # Calculate split indices
    n = len(df)
    test_end = int(n * test_ratio)    
    val_end = test_end + int(n * val_ratio)
    

    # Split the data
    test_data = df.iloc[:test_end].sort_index(ascending=False)
    val_data = df.iloc[test_end:val_end].sort_index(ascending=False)
    train_data = df.iloc[val_end:].sort_index(ascending=False)

    return train_data, val_data, test_data

# Example usage
#Reduce to subset of all rain rows and equal number of no rain rows
#Pick data for about preceding 8 hours
df_transformedn = df_transformed.iloc[:,list(range(0,29)) + list(range(503,1748))]

#df_transformedn = df_transformed
train_data, val_data, test_data = split_time_series_data(df_transformedn)
print("Training Set:", train_data.shape)
print(train_data[0].value_counts(dropna=False).sort_index())
print("Validation Set:", val_data.shape)
print(val_data[0].value_counts(dropna=False).sort_index())
print("Test Set:", test_data.shape)
print(test_data[0].value_counts(dropna=False).sort_index())

Training Set: (76257, 1274)
0
0.0    68763
0.1     2495
0.5     1258
1.0     1280
2.0      680
3.0      409
4.0      300
5.0     1072
Name: count, dtype: int64
Validation Set: (25419, 1274)
0
0.0    22874
0.1      804
0.5      465
1.0      432
2.0      268
3.0      117
4.0       84
5.0      375
Name: count, dtype: int64
Test Set: (25419, 1274)
0
0.0    22949
0.1      807
0.5      450
1.0      425
2.0      226
3.0      141
4.0      102
5.0      319
Name: count, dtype: int64


In [21]:
# Define the station ID and output directory


# Export datasets to Parquet and CSV
train_data.to_parquet(f"{ipd04}{stid_target}_train.parquet", index=False)
val_data.to_parquet(f"{ipd04}{stid_target}_validation.parquet", index=False)
test_data.to_parquet(f"{ipd04}{stid_target}_test.parquet", index=False)

train_data.to_csv(f"{ipd04}{stid_target}_train.csv", index=False)
# val_data.to_csv(f"{ipd04}{stid_target}_validation.csv", index=False)
# test_data.to_csv(f"{ipd04}{stid_target}_test.csv", index=False)

print("Datasets exported successfully.")

#python -m s4model --modelname 72406093721 --trainset C:\\Users\\jhugh\\Documents\\HT\\NCEI_data\\metrics_csv\\72406093721_train.parquet --valset C:\\Users\\jhugh\\Documents\\HT\\NCEI_data\\metrics_csv\\72406093721_validation.parquet --testset C:\\Users\\jhugh\\Documents\\HT\\NCEI_data\\metrics_csv\\72406093721_test.parquet --tabulardata --dependent_variable 0 --epochs 30

# python -m charts --df ../results/72508014740_Test_results_20250424_104121PM.csv --actual 0 --predicted Predicted 
# python -m charts --df ../results/72508014740_Test_results_20250427_100132PM.csv --actual 0 --predicted Predicted 
# python -m charts --df ../results/72508014740_Test_results_20250428_091259PM.csv --actual 0 --predicted Predicted 
# python -m charts --df ../results/72508014740_Test_results_20250428_094033PM.csv --actual 0 --predicted Predicted 
# python -m charts --df ../results/72508014740_Test_results_20250429_091538PM.csv --actual 0 --predicted Predicted

Datasets exported successfully.


In [ ]:
f"{ipd04}{stid_target}_train.csv"

'\\\\CXA01\\Users\\jhugh\\Documents\\Py_S4\\Py_S4_v02_JHH\\NCEI_parquet_files\\74486094789_train.csv'

In [ ]:
#Code to run at cmd
#python -m s4model --modelname 72406093721 --trainset C:\\Users\\jhugh\\Documents\\HT\\NCEI_data\\metrics_csv\\72406093721_train.parquet --valset C:\\Users\\jhugh\\Documents\\HT\\NCEI_data\\metrics_csv\\72406093721_validation.parquet --testset C:\\Users\\jhugh\\Documents\\HT\\NCEI_data\\metrics_csv\\72406093721_test.parquet --tabulardata --dependent_variable 0 --epochs 30


In [ ]:
# def find_first_non_nan(vector):
#     return next((i for i, x in enumerate(vector) if not math.isnan(x)), None)

# first_number_at1 = find_first_non_nan(vc_at1)
# first_number_rh1 = find_first_non_nan(vc_rh1)
# first_number_rh2 = find_first_non_nan(vc_rh2)
# first_number_rh3 = find_first_non_nan(vc_rh3)
# first_number_pr1 = find_first_non_nan(vc_pr1)

# #Number of missing data points
# print(f"AT1 Number of missing cells: {np.count_nonzero(np.isnan(vc_at1))}")
# print(f"AT1 Vector Length: {len(vc_at1)}")

# print(f"RH1 Number of missing cells: {np.count_nonzero(np.isnan(vc_rh1))}")
# print(f"RH1 Vector Length: {len(vc_rh1)}")

# print(f"PR1 Number of missing cells: {np.count_nonzero(np.isnan(vc_pr1))}")
# print(f"PR1 Vector Length: {len(vc_pr1)}")

# #Once a day metrics
# v_data_first_once_day = max(
#                    first_number_rh1,
#                    first_number_rh2,
#                    first_number_rh3)
# print(v_data_first_once_day)

# #24 times a day metrics
# v_data_first_24h_day = max(first_number_at1,
#                    first_number_pr1)
# print(v_data_first_24h_day)


#These vectors all start with a numeric value so missing values can be filled


#print(first_number_at1)
#print(first_number_rh1)
#print(first_number_rh2)
#print(first_number_rh3)
#print(first_number_pr1)



In [ ]:
df = pd.DataFrame(jj)
fc = df.iloc[:,0].astype('float32')
print(fc.shape)
import matplotlib.pyplot as plt

plt.hist(fc, bins=50, color='blue', alpha=0.7, density=True)
plt.title('Normalized Histogram of a')
plt.xlabel('Value')
plt.ylabel('Density')
plt.show()

In [ ]:
# Custom bins

a = fc[~fc.isnull()]

# Calculate min, max, and percentiles by 10 for 'a'
min_val = a.min()
max_val = a.max()
percentiles = np.percentile(a, np.arange(0, 101, 10))

print(f"Min: {min_val}")
print(f"Max: {max_val}")
print(f"Percentiles: {percentiles}")
